<a href="https://colab.research.google.com/github/jespimentel/dados_criminais_ssp_sp/blob/main/dados_criminais.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import ipywidgets as widgets
import folium
from folium.plugins import MarkerCluster

In [ ]:
%%time
df = pd.read_excel('SPDadosCriminais_2024.xlsx')

/usr/local/lib/python3.10/dist-packages/openpyxl/worksheet/_reader.py:329: UserWarning: Data Validation extension is not supported and will be removed
  warn(msg)


CPU times: user 4min 22s, sys: 2.38 s, total: 4min 25s
Wall time: 4min 30s


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 689645 entries, 0 to 689644
Data columns (total 25 columns):
 #   Column                           Non-Null Count   Dtype         
---  ------                           --------------   -----         
 0   NOME_DEPARTAMENTO                689645 non-null  object        
 1   NOME_SECCIONAL                   689645 non-null  object        
 2   NOME_DELEGACIA                   689645 non-null  object        
 3   CIDADE                           689645 non-null  object        
 4   ANO_BO                           689645 non-null  int64         
 5   NUM_BO                           689645 non-null  object        
 6   DATA_COMUNICACAO                 689644 non-null  object        
 7   DATA_OCORRENCIA_BO               689631 non-null  datetime64[ns]
 8   HORA_OCORRENCIA_BO               485370 non-null  object        
 9   DESC_PERIODO                     204274 non-null  object        
 10  DESCR_TIPOLOCAL                  677905 non-

In [ ]:
options=df['NOME_MUNICIPIO_CIRCUNSCRIÇÃO'].unique().tolist()
options.sort()

municipio = widgets.Dropdown(
    options=options,
    value='PIRACICABA',
    description='Município:',
    disabled=False,
)
display(municipio)

Dropdown(description='Município:', index=435, options=('ADAMANTINA', 'ADOLFO', 'AGUAI', 'AGUAS DA PRATA', 'AGU…

In [ ]:
filtro = df['NOME_MUNICIPIO_CIRCUNSCRIÇÃO'] == municipio.value
df_filtrado = df.loc[filtro].copy()

# Criando a coluna 'HORARIO' e 'DIA_DA_SEMANA'
df_filtrado.loc[:, 'HORARIO'] = df_filtrado['HORA_OCORRENCIA_BO'].astype(str).str.slice(0, 2)
df_filtrado.loc[:, 'DIA_DA_SEMANA'] = df_filtrado['DATA_OCORRENCIA_BO'].dt.day_name()

traducao_dias_semana = {
    'Monday': 'Segunda-feira',
    'Tuesday': 'Terça-feira',
    'Wednesday': 'Quarta-feira',
    'Thursday': 'Quinta-feira',
    'Friday': 'Sexta-feira',
    'Saturday': 'Sábado',
    'Sunday': 'Domingo'
}

df_filtrado['DIA_DA_SEMANA'] = df_filtrado['DIA_DA_SEMANA'].map(traducao_dias_semana)

# Selecionando as colunas de interesse
colunas_de_interesse = ['NUM_BO', 'DATA_OCORRENCIA_BO', 'DIA_DA_SEMANA', 'HORARIO', 'DESCR_TIPOLOCAL',
                        'BAIRRO', 'LATITUDE', 'LONGITUDE', 'NOME_DELEGACIA_CIRCUNSCRIÇÃO', 'NATUREZA_APURADA']

df_filtrado = df_filtrado.loc[:, colunas_de_interesse]
df_filtrado.sample(5)

NUM_BO DATA_OCORRENCIA_BO  DIA_DA_SEMANA HORARIO DESCR_TIPOLOCAL  \
276104  DR6665         2024-03-15    Sexta-feira      10     Via Pública   
475907  GO9304         2024-05-13  Segunda-feira      18     Via Pública   
79672   BL1000         2024-01-31   Quarta-feira      00     Via Pública   
276087  DN0173         2024-03-12    Terça-feira      10     Via Pública   
573693  IS7765         2024-06-14    Sexta-feira      23     Metalúrgica   

              BAIRRO   LATITUDE  LONGITUDE NOME_DELEGACIA_CIRCUNSCRIÇÃO  \
276104  MONTE LIBANO -22.754076 -47.649973          03º D.P. PIRACICABA   
475907     SÃO DIMAS -22.715881 -47.645242          01º D.P. PIRACICABA   
79672           ALTO -22.726801 -47.644655          02º D.P. PIRACICABA   
276087  MONTE LIBANO -22.757523 -47.653415          03º D.P. PIRACICABA   
573693    AREA RURAL -22.654798 -47.790962          05º D.P. PIRACICABA   

                                       NATUREZA_APURADA  
276104                         TRÁFICO DE ENTORPECENTES  
475907                                 FURTO DE VEÍCULO  
79672   LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO  
276087                           PORTE DE ENTORPECENTES  
573693                                 FURTO DE VEÍCULO

In [ ]:
df_filtrado['NATUREZA_APURADA'].value_counts()

NATUREZA_APURADA
FURTO - OUTROS                                     2149
LESÃO CORPORAL DOLOSA                               760
FURTO DE VEÍCULO                                    418
TRÁFICO DE ENTORPECENTES                            413
LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO     381
ROUBO - OUTROS                                      240
ROUBO DE VEÍCULO                                     74
HOMICÍDIO CULPOSO POR ACIDENTE DE TRÂNSITO           33
PORTE DE ENTORPECENTES                               32
LESÃO CORPORAL CULPOSA - OUTRAS                      19
PORTE DE ARMA                                        19
TENTATIVA DE HOMICÍDIO                               18
HOMICÍDIO DOLOSO                                     15
ESTUPRO DE VULNERÁVEL                                14
APREENSÃO DE ENTORPECENTES                           10
ROUBO DE CARGA                                        7
ESTUPRO                                               5
HOMICIDIO CULPOSO POR ACIDENTE DE TRANSITO            2
Name: count, dtype: int64

In [ ]:
df_filtrado_georreferenciado = df_filtrado[(~df_filtrado['LATITUDE'].isna()) & (df_filtrado['LATITUDE'] != 0)]
df_filtrado_georreferenciado['NATUREZA_APURADA'].value_counts()

NATUREZA_APURADA
FURTO - OUTROS                                     647
TRÁFICO DE ENTORPECENTES                           359
LESÃO CORPORAL DOLOSA                              306
LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO    304
FURTO DE VEÍCULO                                   240
ROUBO - OUTROS                                     114
ROUBO DE VEÍCULO                                    63
HOMICÍDIO CULPOSO POR ACIDENTE DE TRÂNSITO          32
PORTE DE ENTORPECENTES                              21
TENTATIVA DE HOMICÍDIO                              14
HOMICÍDIO DOLOSO                                    11
PORTE DE ARMA                                       10
APREENSÃO DE ENTORPECENTES                           9
ROUBO DE CARGA                                       7
LESÃO CORPORAL CULPOSA - OUTRAS                      2
ESTUPRO                                              2
ESTUPRO DE VULNERÁVEL                                2
HOMICIDIO CULPOSO POR ACIDENTE DE TRANSITO           2
Name: count, dtype: int64

In [ ]:
df_filtrado_georreferenciado.to_csv('dados_criminais_filtrados.csv')

In [ ]:
df_filtrado_georreferenciado.head(3)

NUM_BO DATA_OCORRENCIA_BO  DIA_DA_SEMANA HORARIO DESCR_TIPOLOCAL  \
79516  AC2270         2023-12-27   Quarta-feira      10     Via Pública   
79517  AC7871         2024-01-01  Segunda-feira      06     Via Pública   
79526  AG6709         2024-01-04   Quinta-feira      na    Bar/Botequim   

          BAIRRO   LATITUDE  LONGITUDE NOME_DELEGACIA_CIRCUNSCRIÇÃO  \
79516     CENTRO -22.730664 -47.650531          01º D.P. PIRACICABA   
79517     CENTRO -22.735537 -47.655385          01º D.P. PIRACICABA   
79526  SÃO DIMAS -22.712891 -47.636277          01º D.P. PIRACICABA   

      NATUREZA_APURADA  
79516   FURTO - OUTROS  
79517   FURTO - OUTROS  
79526   FURTO - OUTROS

In [ ]:
options=df_filtrado_georreferenciado['NATUREZA_APURADA'].unique().tolist()
options.sort()
options.append('TODOS')

# Seleção múltipla
crime = widgets.SelectMultiple(
    options=options,
    value=['TODOS'],  # Valor inicial
    description='Natureza:',
    disabled=False
)
display(crime)

SelectMultiple(description='Natureza:', index=(18,), options=('APREENSÃO DE ENTORPECENTES', 'ESTUPRO', 'ESTUPR…

In [ ]:
if 'TODOS' in crime.value:
  df_filtrado_georreferenciado_por_crime = df_filtrado_georreferenciado
else:
    filtro = df_filtrado_georreferenciado['NATUREZA_APURADA'].isin(crime.value)
    df_filtrado_georreferenciado_por_crime = df_filtrado_georreferenciado.loc[filtro].copy()

In [ ]:
df_filtrado_georreferenciado_por_crime.sample(5)

NUM_BO DATA_OCORRENCIA_BO DIA_DA_SEMANA HORARIO DESCR_TIPOLOCAL  \
573311  HO2012         2024-05-28   Terça-feira      na     Via Pública   
653575  KF1704         2024-07-27        Sábado      01     Via Pública   
653568  JN3154         2024-07-10  Quarta-feira      17     Via Pública   
176723  BR9777         2024-02-04       Domingo      14     Restaurante   
476483  GV3434         2024-05-18        Sábado      13     Via Pública   

                 BAIRRO   LATITUDE  LONGITUDE NOME_DELEGACIA_CIRCUNSCRIÇÃO  \
573311           CENTRO -22.730664 -47.650531          01º D.P. PIRACICABA   
653575             ALTO -22.723959 -47.642820          02º D.P. PIRACICABA   
653568        SÃO JUDAS -22.729659 -47.636340          02º D.P. PIRACICABA   
176723      CIDADE ALTA -22.735372 -47.640322          02º D.P. PIRACICABA   
476483  JARDIM PLANALTO -22.745606 -47.676112          07º D.P. PIRACICABA   

                                       NATUREZA_APURADA  
573311                            LESÃO CORPORAL DOLOSA  
653575  LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO  
653568  LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO  
176723                            LESÃO CORPORAL DOLOSA  
476483                         TRÁFICO DE ENTORPECENTES

In [ ]:
df_filtrado_georreferenciado_por_crime['NATUREZA_APURADA'].unique().tolist()

['FURTO - OUTROS',
 'FURTO DE VEÍCULO',
 'LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO',
 'LESÃO CORPORAL DOLOSA',
 'ROUBO - OUTROS',
 'TRÁFICO DE ENTORPECENTES',
 'HOMICÍDIO CULPOSO POR ACIDENTE DE TRÂNSITO',
 'HOMICÍDIO DOLOSO',
 'ROUBO DE VEÍCULO',
 'PORTE DE ENTORPECENTES',
 'TENTATIVA DE HOMICÍDIO',
 'PORTE DE ARMA',
 'ROUBO DE CARGA',
 'LESÃO CORPORAL CULPOSA - OUTRAS',
 'APREENSÃO DE ENTORPECENTES',
 'ESTUPRO',
 'ESTUPRO DE VULNERÁVEL',
 'HOMICIDIO CULPOSO POR ACIDENTE DE TRANSITO']

In [ ]:
df_filtrado_georreferenciado_por_crime = df_filtrado_georreferenciado_por_crime.loc[df_filtrado_georreferenciado_por_crime['DATA_OCORRENCIA_BO'].notnull()]

In [ ]:
def gera_mapa_clusterizado(df):
  COORDENADAS_MEDIAS = df['LATITUDE'].mean(), df['LONGITUDE'].mean()
  # Cria o mapa vazio
  mapa = folium.Map(location=COORDENADAS_MEDIAS, zoom_start=10)

  # Cria um MarkerCluster para agrupar os marcadores
  marker_cluster = MarkerCluster().add_to(mapa)

  # Cria um dicionário de cores para os marcadores
  cores = {
      'TRÁFICO DE ENTORPECENTES': 'black',
      'PORTE DE ARMA': 'gray',
      'HOMICÍDIO DOLOSO': 'darkred',
      'TENTATIVA DE HOMICÍDIO': 'red',
      'LESÃO CORPORAL DOLOSA': 'lightred',
      'ROUBO DE VEÍCULO':'darkblue',
      'FURTO DE VEÍCULO': 'blue',
      'HOMICÍDIO CULPOSO POR ACIDENTE DE TRÂNSITO':'darkgreen',
      'HOMICIDIO CULPOSO POR ACIDENTE DE TRANSITO': 'darkgreen',
      'LESÃO CORPORAL CULPOSA POR ACIDENTE DE TRÂNSITO': 'green'
  }

  # Cor padrão para naturezas não especificadas
  cor_padrao = 'beige'

  # Adiciona os marcadores
  for _, row in df.iterrows():

    html_popup = f"""
    <strong>{row['NATUREZA_APURADA']}</strong> <br>
    {row['DATA_OCORRENCIA_BO'].strftime('%d/%m/%Y')}<br>
    {row['DIA_DA_SEMANA']}<br>
    <strong>BO nº {row['NUM_BO']}</strong>
    """
    # Determina a cor do marcador com base na natureza
    cor = cores.get(row['NATUREZA_APURADA'], cor_padrao)

    folium.Marker(
        location=[row['LATITUDE'], row['LONGITUDE']],
        popup=html_popup,
        icon=folium.Icon(color=cor, icon='info-sign')
    ).add_to(marker_cluster)

  return mapa

mapa = gera_mapa_clusterizado(df_filtrado_georreferenciado_por_crime)
mapa.save('mapa_clusterizado.html')
display(mapa)